# 1) Import some usefull packages

In [1]:
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
import geopy.distance
import requests
import folium
import json
import wget
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

These following packages were installed only one time

In [2]:
# conda install -c conda-forge geopy
# !conda install -c conda-forge folium
# pip install wget
# pip install urllib2

# 2) Extract cities around Chassieu (25 km radius)

Get data from all cities (around 37000) in France using this link: https://public.opendatasoft.com/explore/dataset/code-insee-postaux-geoflar/export/?flg=fr

In [3]:
df = pd.read_csv(r'C:\Users\a018325\OneDrive - Alliance\Doc perso\Datas\Exam cours 9\code-insee-postaux-geoflar.csv',delimiter=";", error_bad_lines=False, na_filter = True)
df.head()

C:\Users\a018325\AppData\Local\Continuum\anaconda3\lib\site-packages\IPython\core\interactiveshell.py:3058: DtypeWarning: Columns (0,11) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


CODE INSEE   NOM DE LA COMMUNE  CODE POSTAL LIBELLE D'ACHEMINEMENT  \
0       1053     BOURG EN BRESSE         1000        BOURG EN BRESSE   
1       1344  ST DENIS LES BOURG         1000     ST DENIS LES BOURG   
2       1165        FRANCHELEINS         1090           FRANCHELEINS   
3       1169         GENOUILLEUX         1090            GENOUILLEUX   
4       1183            GUEREINS         1090               GUEREINS   

   Y Centroid   Nom Region Nom Dept          STATUT  Code Region  \
0     65697.0  RHONE-ALPES      AIN      Préfecture         82.0   
1     65702.0  RHONE-ALPES      AIN  Commune simple         82.0   
2     65542.0  RHONE-ALPES      AIN  Commune simple         82.0   
3     65593.0  RHONE-ALPES      AIN  Commune simple         82.0   
4     65578.0  RHONE-ALPES      AIN  Commune simple         82.0   

   Code Commune  ...                 Geometry X Y  \
0          53.0  ...  46.2051520382,5.24602125501   
1         344.0  ...  46.2111998453,5.18462806771   
2         165.0  ...  46.0735946256,4.81293575559   
3         169.0  ...  46.1201611728,4.79288195016   
4         183.0  ...   46.106624674,4.78159420118   

                                            Geometry  Id Geofla X Chef Lieu  \
0  {"type": "Polygon", "coordinates": [[[5.256739...     5244.0      8717.0   
1  {"type": "Polygon", "coordinates": [[[5.206996...     7690.0      8690.0   
2  {"type": "Polygon", "coordinates": [[[4.800546...    12920.0      8397.0   
3  {"type": "Polygon", "coordinates": [[[4.805930...    30192.0      8379.0   
4  {"type": "Polygon", "coordinates": [[[4.770749...    19498.0      8375.0   

  Code Canton  Superficie  Population            Nom Commune  \
0        99.0      2400.0        39.6        BOURG-EN-BRESSE   
1        43.0      1261.0         5.4  SAINT-DENIS-LES-BOURG   
2        30.0      1361.0         1.3           FRANCHELEINS   
3        32.0       409.0         0.6            GENOUILLEUX   
4        32.0       441.0         1.3               GUEREINS   

   Code Arrondissement  Y Chef Lieu  
0                  2.0      65696.0  
1                  2.0      65689.0  
2                  2.0      65542.0  
3                  2.0      65592.0  
4                  2.0      65580.0  

[5 rows x 23 columns]

Following code is made to convert 4 digit insee code into 5 digit one, because insee code will be used as a link 
with geojson files (and geojson files are only 5 digit codes)

Then, we have to extract usefull informations: we will only keep 3 departements (on 100) because the location I'm focused on is the city of Chassieu and Chassieu is close to 3 departments (Rhone, Ain and Isere)

In [4]:
for i in range(5000):
    if len(df['CODE INSEE'][i]) == 4:
        df['CODE INSEE'][i] = '0' + df['CODE INSEE'][i]

df_3dept = df[(df['Nom Dept'] == ('RHONE')) | (df['Nom Dept'] == ('AIN')) | (df['Nom Dept'] == ('ISERE'))]
df_3dept = df_3dept.reset_index()
df_3dept.head()

C:\Users\a018325\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  This is separate from the ipykernel package so we can avoid doing imports until


index CODE INSEE   NOM DE LA COMMUNE  CODE POSTAL LIBELLE D'ACHEMINEMENT  \
0      0      01053     BOURG EN BRESSE         1000        BOURG EN BRESSE   
1      1      01344  ST DENIS LES BOURG         1000     ST DENIS LES BOURG   
2      2      01165        FRANCHELEINS         1090           FRANCHELEINS   
3      3      01169         GENOUILLEUX         1090            GENOUILLEUX   
4      4      01183            GUEREINS         1090               GUEREINS   

   Y Centroid   Nom Region Nom Dept          STATUT  Code Region  ...  \
0     65697.0  RHONE-ALPES      AIN      Préfecture         82.0  ...   
1     65702.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
2     65542.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
3     65593.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
4     65578.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   

                  Geometry X Y  \
0  46.2051520382,5.24602125501   
1  46.2111998453,5.18462806771   
2  46.0735946256,4.81293575559   
3  46.1201611728,4.79288195016   
4   46.106624674,4.78159420118   

                                            Geometry Id Geofla  X Chef Lieu  \
0  {"type": "Polygon", "coordinates": [[[5.256739...    5244.0       8717.0   
1  {"type": "Polygon", "coordinates": [[[5.206996...    7690.0       8690.0   
2  {"type": "Polygon", "coordinates": [[[4.800546...   12920.0       8397.0   
3  {"type": "Polygon", "coordinates": [[[4.805930...   30192.0       8379.0   
4  {"type": "Polygon", "coordinates": [[[4.770749...   19498.0       8375.0   

  Code Canton Superficie  Population            Nom Commune  \
0        99.0     2400.0        39.6        BOURG-EN-BRESSE   
1        43.0     1261.0         5.4  SAINT-DENIS-LES-BOURG   
2        30.0     1361.0         1.3           FRANCHELEINS   
3        32.0      409.0         0.6            GENOUILLEUX   
4        32.0      441.0         1.3               GUEREINS   

   Code Arrondissement  Y Chef Lieu  
0                  2.0      65696.0  
1                  2.0      65689.0  
2                  2.0      65542.0  
3                  2.0      65592.0  
4                  2.0      65580.0  

[5 rows x 24 columns]

There are 1256 cities in these 3 departments

We will select only cities which are less than 25km from Chassieu center but before, we have to create a longitude and latitude column in the dataframe by using Geométry X Y column


In [5]:
latitude = []
longitude = []
for i in range(df_3dept['Geometry X Y'].str.split(",").size):
    latitude.append(float(df_3dept['Geometry X Y'].str.split(",")[i][0]))
    longitude.append(float(df_3dept['Geometry X Y'].str.split(",")[i][1]))
    
df_3dept ['latitude'] = latitude
df_3dept ['longitude'] = longitude
df_3dept=df_3dept.drop('Geometry X Y', axis = 1)
df_3dept.head()

index CODE INSEE   NOM DE LA COMMUNE  CODE POSTAL LIBELLE D'ACHEMINEMENT  \
0      0      01053     BOURG EN BRESSE         1000        BOURG EN BRESSE   
1      1      01344  ST DENIS LES BOURG         1000     ST DENIS LES BOURG   
2      2      01165        FRANCHELEINS         1090           FRANCHELEINS   
3      3      01169         GENOUILLEUX         1090            GENOUILLEUX   
4      4      01183            GUEREINS         1090               GUEREINS   

   Y Centroid   Nom Region Nom Dept          STATUT  Code Region  ...  \
0     65697.0  RHONE-ALPES      AIN      Préfecture         82.0  ...   
1     65702.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
2     65542.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
3     65593.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   
4     65578.0  RHONE-ALPES      AIN  Commune simple         82.0  ...   

   Id Geofla  X Chef Lieu Code Canton  Superficie Population  \
0     5244.0       8717.0        99.0      2400.0       39.6   
1     7690.0       8690.0        43.0      1261.0        5.4   
2    12920.0       8397.0        30.0      1361.0        1.3   
3    30192.0       8379.0        32.0       409.0        0.6   
4    19498.0       8375.0        32.0       441.0        1.3   

             Nom Commune  Code Arrondissement  Y Chef Lieu   latitude  \
0        BOURG-EN-BRESSE                  2.0      65696.0  46.205152   
1  SAINT-DENIS-LES-BOURG                  2.0      65689.0  46.211200   
2           FRANCHELEINS                  2.0      65542.0  46.073595   
3            GENOUILLEUX                  2.0      65592.0  46.120161   
4               GUEREINS                  2.0      65580.0  46.106625   

   longitude  
0   5.246021  
1   5.184628  
2   4.812936  
3   4.792882  
4   4.781594  

[5 rows x 25 columns]

 We now calculate the distance between Chassieu center and each city, in order to remove those which are more than 25 km away

In [6]:
Distance_from_chassieu = []
coords_chassieu = (45.7314009,4.9638613)
                  
for i in range(df_3dept['NOM DE LA COMMUNE'].str.split(",").size):
    coords = (df_3dept['latitude'][i],df_3dept['longitude'][i])
    distance = geopy.distance.geodesic(coords, coords_chassieu).km 
    Distance_from_chassieu.append(distance) 
                  
df_3dept ['Distance from chassieu'] = Distance_from_chassieu

# We call df_25km the list of cities which are less than 25km far from Meyzieu

df_25km = df_3dept[df_3dept['Distance from chassieu']<25]
df_25km = df_25km.reset_index()
df_25km.head()

level_0  index CODE INSEE NOM DE LA COMMUNE  CODE POSTAL  \
0       25     25      01049         LA BOISSE         1120   
1       26     26      01142           DAGNEUX         1120   
2       27     27      01262          MONTLUEL         1120   
3       28     28      01276           NIEVROZ         1120   
4       29     29      01297             PIZAY         1120   

  LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept            STATUT  \
0              LA BOISSE     65292.0  RHONE-ALPES      AIN    Commune simple   
1                DAGNEUX     65302.0  RHONE-ALPES      AIN    Commune simple   
2               MONTLUEL     65343.0  RHONE-ALPES      AIN  Chef-lieu canton   
3                NIEVROZ     65268.0  RHONE-ALPES      AIN    Commune simple   
4                  PIZAY     65347.0  RHONE-ALPES      AIN    Commune simple   

   ...  X Chef Lieu  Code Canton  Superficie Population  Nom Commune  \
0  ...       8579.0         20.0       938.0        2.9    LA BOISSE   
1  ...       8604.0         20.0       683.0        4.0      DAGNEUX   
2  ...       8595.0         20.0      4009.0        6.9     MONTLUEL   
3  ...       8602.0         20.0      1050.0        1.5      NIEVROZ   
4  ...       8620.0         20.0      1118.0        0.8        PIZAY   

  Code Arrondissement  Y Chef Lieu   latitude  longitude  \
0                 2.0      65289.0  45.844621   5.027832   
1                 2.0      65301.0  45.853162   5.072892   
2                 2.0      65300.0  45.890901   5.019876   
3                 2.0      65272.0  45.822294   5.059496   
4                 2.0      65342.0  45.892851   5.089155   

   Distance from chassieu  
0               13.531591  
1               15.969300  
2               18.254808  
3               12.545249  
4               20.416965  

[5 rows x 27 columns]

In [7]:
# define the world map centered around Chassieu with a low zoom level
world_map = folium.Map(location=coords_chassieu, zoom_start=10)

# instantiate a feature group for the cities in the dataframe
cities_25km = folium.map.FeatureGroup()

# loop through the 100 crimes and add each to the incidents feature group
for lat, lng, in zip(df_25km.latitude, df_25km.longitude):
    cities_25km.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5, # define how big you want the circle markers to be
            color='blue',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )
    
folium.features.Circle(coords_chassieu, 
                        color='yellow',
                        radius = 25000 ).add_to(world_map)

# add incidents to map
world_map.add_child(cities_25km)

# 3. Restrict cities which are at less than 25 min of car (average) using Google API

In [8]:
# Use Google API in order to obtain the duration 

time_in_car_to_chassieu = []
time_in_car_from_chassieu = []

# enter your api key here 
api_key = ''

for i in range(df_25km['NOM DE LA COMMUNE'].str.split(",").size):
    
    # Take source as input 
    source = str(df_25km['latitude'][i])+','+str(df_25km['longitude'][i])

    # Take destination as input 
    dest = str(coords_chassieu[0])+','+str(coords_chassieu[1])
    
    # url variable store url  
    url ='https://maps.googleapis.com/maps/api/distancematrix/json?'

    # Get method of requests module 
    # return response object 
    r_to = requests.get(url + 'origins=' + source +
                     '&destinations=' + dest +
                       '&key=' + api_key) 
    
    # Get method of requests module 
    # return response object 
    r_from = requests.get(url + 'origins=' + dest +
                     '&destinations=' + source +
                       '&key=' + api_key) 

    # json method of response object 
    # return json format result 
    time_in_car_to_chassieu.append(r_to.json()) 
    time_in_car_from_chassieu.append(r_from.json()) 
    

From the data extracted from google, we can extract the time and km of travel for each city in both going and returns.

Finally, we make a average of these 2 numbers in order to have only one number to follow and because 
they are quite close to each other

In [9]:
time_distance_df = pd.DataFrame(columns = ['City', 'Distance from chassieu in km', 'Time from chassieu in min', 
                                                  'Distance to chassieu in km', 'Time to chassieu in min'])

for i in range(df_25km['NOM DE LA COMMUNE'].str.split(",").size):    
    
    City = df_25km['NOM DE LA COMMUNE'][i]
    
    if df_25km['NOM DE LA COMMUNE'][i] == "CHASSIEU":
        time_distance_df.loc[len(time_distance_df)] = [City, 0, 0, 0, 0]
        
    else:
        Distance_from_chassieu = float(time_in_car_from_chassieu[i]['rows'][0]['elements'][0]['distance']['text'][0:2])
        Time_from_chassieu = float(time_in_car_from_chassieu[i]['rows'][0]['elements'][0]['duration']['text'][0:2])
        Distance_to_chassieu = float(time_in_car_to_chassieu[i]['rows'][0]['elements'][0]['distance']['text'][0:2])
        Time_to_chassieu = float(time_in_car_to_chassieu[i]['rows'][0]['elements'][0]['duration']['text'][0:2])
    
        time_distance_df.loc[len(time_distance_df)] = [City, Distance_from_chassieu, Time_from_chassieu, Distance_to_chassieu, Time_to_chassieu]

        
time_distance_df['Distance chassieu (km)'] = (time_distance_df['Distance from chassieu in km']+time_distance_df['Distance to chassieu in km'])/2
time_distance_df['Time chassieu (min)'] = (time_distance_df['Time from chassieu in min']+time_distance_df['Time to chassieu in min'])/2

time_distance_df = time_distance_df.drop(['Distance from chassieu in km','Distance to chassieu in km','Time to chassieu in min','Time from chassieu in min'], axis = 1)
time_distance_df.head()

City  Distance chassieu (km)  Time chassieu (min)
0  LA BOISSE                    24.5                 26.0
1    DAGNEUX                    25.0                 27.5
2   MONTLUEL                    31.5                 35.0
3    NIEVROZ                    21.0                 25.0
4      PIZAY                    30.5                 33.5

In [10]:
# We now add this data to df_25km 

df_25km['Distance chassieu (km)'] = time_distance_df['Distance chassieu (km)']
df_25km['Time chassieu (min)'] = time_distance_df['Time chassieu (min)']

# We remove all cities which are further than 25 min away, this gives the new dataframe df_25min

df_25min = df_25km[df_25km['Time chassieu (min)']<25]
df_25min.describe()

level_0         index   CODE POSTAL    Y Centroid  Code Region  \
count    62.000000     62.000000     62.000000     62.000000         62.0   
mean    918.000000  23654.161290  58017.064516  65147.048387         82.0   
std     261.611275   8391.671324  19768.723936     82.590125          0.0   
min     392.000000    395.000000   1700.000000  65009.000000         82.0   
25%     771.250000  15068.250000  38540.000000  65071.250000         82.0   
50%    1018.000000  28506.000000  69285.000000  65143.000000         82.0   
75%    1055.500000  28543.500000  69390.000000  65214.500000         82.0   
max    1246.000000  28734.000000  69970.000000  65307.000000         82.0   

       Code Commune     Z Moyen   X Centroid     Id Geofla  X Chef Lieu  \
count     62.000000   62.000000    62.000000     62.000000    62.000000   
mean     270.225806  224.919355  8526.451613  21597.048387  8526.467742   
std      124.607110   36.809789    92.066917  10308.695609    92.943085   
min       11.000000  166.000000  8393.000000    501.000000  8397.000000   
25%      211.500000  197.250000  8452.250000  14825.000000  8446.250000   
50%      280.500000  219.500000  8511.000000  21454.500000  8510.000000   
75%      296.750000  247.000000  8605.500000  30433.250000  8606.750000   
max      557.000000  352.000000  8703.000000  36613.000000  8700.000000   

       Code Canton   Superficie  Population  Code Arrondissement  \
count    62.000000    62.000000   62.000000            62.000000   
mean     46.451613  1185.032258   16.725806             1.419355   
std      20.781989   688.065665   26.100197             0.713991   
min       8.000000   185.000000    1.000000             1.000000   
25%      37.250000   684.250000    2.650000             1.000000   
50%      40.000000  1039.000000    5.200000             1.000000   
75%      48.000000  1473.750000   15.525000             2.000000   
max      99.000000  2966.000000  144.800000             3.000000   

        Y Chef Lieu   latitude  longitude  Distance from chassieu  \
count     62.000000  62.000000  62.000000               62.000000   
mean   65146.370968  45.715181   4.962998               11.623959   
std       81.963053   0.074455   0.118087                4.358882   
min    65009.000000  45.588634   4.789796                0.710319   
25%    65070.250000  45.649743   4.868899                8.553084   
50%    65142.000000  45.710787   4.944944               11.730454   
75%    65205.750000  45.776030   5.065533               14.387073   
max    65298.000000  45.860340   5.185985               21.571059   

       Distance chassieu (km)  Time chassieu (min)  
count               62.000000            62.000000  
mean                16.814516            19.096774  
std                  6.400713             4.962019  
min                  0.000000             0.000000  
25%                 11.875000            17.000000  
50%                 17.500000            20.250000  
75%                 21.375000            22.875000  
max                 28.500000            24.500000

We have now only 62 cities which are closer than 25 minutes (in car) from Massieu

In [11]:
# lets plot a map of these cities

world_map = folium.Map(location=coords_chassieu, zoom_start=10)

# instantiate a feature group for the incidents in the dataframe
incidents = folium.map.FeatureGroup()

# loop through the 100 crimes and add each to the incidents feature group
for lat, lng, in zip(df_25min.latitude, df_25min.longitude):
    incidents.add_child(
        folium.features.CircleMarker(
            [lat, lng],
            radius=5, # define how big you want the circle markers to be
            color='blue',
            fill=True,
            fill_color='blue',
            fill_opacity=0.6
        )
    )
    
folium.features.Circle(coords_chassieu, 
                        color='yellow',
                        radius = 25000 ).add_to(world_map)

# add incidents to map
world_map.add_child(incidents)

Import cities boundaries, from a file I downloaded from internet, I modified it manually but it is possible to do it automatically

In [12]:
with open(r'C:\Users\a018325\OneDrive - Alliance\Doc perso\Datas\Exam cours 9\communes-01-ain.geojson') as f:
    cities_json = json.load(f)

We create a key to use Geojson file (for the map). Next code is not perfect, but I don't have to courage to change it :)

In [13]:
df_test = pd.DataFrame(columns = ['CODE INSEE'])
df_test2 = pd.DataFrame(columns = ['CODE INSEE','Time chassieu (min)'])
df_test['CODE INSEE']= df['CODE INSEE']
df_test2['CODE INSEE']= df_25min['CODE INSEE']
df_test2['Time chassieu (min)']= df_25min['Time chassieu (min)']

df_test3 = pd.concat([df_test, df_test2], ignore_index = True)

# We remove all NaN values
df_test3.fillna(28, inplace = True)
df_test3 = df_test3[df_test3['Time chassieu (min)'] <26]

df_test3.head()

C:\Users\a018325\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:7: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  import sys


CODE INSEE  Time chassieu (min)
36828      01043                 24.5
36829      01249                 22.5
36830      01275                 18.5
36831      01376                 24.5
36832      38449                 18.0

The next code will create a choropleth map with color related to travel time in car for each cities 

In [14]:
world_map2 = folium.Map(location=coords_chassieu, zoom_start=11)

world_map2.choropleth(
    geo_data= cities_json,
    data= df_test3,
    columns=['CODE INSEE', 'Time chassieu (min)'],
    key_on='feature.properties.code',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.3,
    legend_name='Travel time from chassieu'
)

# display map
world_map2

# 4. Foursquare utilization

From there, I will put less comment when I'm doing almost the same thing than "New York lab"

I will focus my comment on specific action I had to make to adapt this method to my dataset!

In [15]:
CLIENT_ID = '' # your Foursquare ID
CLIENT_SECRET = '' # your Foursquare Secret
VERSION = '20180604'
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: UR3D3SGSL0AZOAWOSJ0U421IK3AC5YYUYKKGWYK4YNBA14CF
CLIENT_SECRET:GABZXPT3UNKO4JFEXCFCTZKNYHYF1Q1YB4QT24RYQTX3ZYOW


We have to adapt our analysis to this particular case study
In fact, cities can be large, and with few venues because chassieu is in the exterior est part of Lyon, which is not the biggest city of the world (around 1,5 million inhabitants).

In [16]:
latitude = coords_chassieu[0]
longitude = coords_chassieu[1]
radius = 1500
intent = 'global'

url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&intent={}'.format(CLIENT_ID, CLIENT_SECRET, latitude, longitude, VERSION, radius, intent)
url

'https://api.foursquare.com/v2/venues/explore?client_id=UR3D3SGSL0AZOAWOSJ0U421IK3AC5YYUYKKGWYK4YNBA14CF&client_secret=GABZXPT3UNKO4JFEXCFCTZKNYHYF1Q1YB4QT24RYQTX3ZYOW&ll=45.7314009,4.9638613&v=20180604&radius=1500&intent=global'

In [17]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5d9703d6e0c0c9002c325b39'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Chassieu',
  'headerFullLocation': 'Chassieu, Lyon',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 10,
  'suggestedBounds': {'ne': {'lat': 45.74490091350001,
    'lng': 4.983165547103828},
   'sw': {'lat': 45.71790088649998, 'lng': 4.9445570528961715}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '504e1ee3e4b062c864a51c6b',
       'name': 'Hotel Chassieu Best Western plus',
       'location': {'address': '82 Route De Lyon',
        'lat': 45.737892733149216,
        'lng': 4.96821315955458,
        'labeledLatLngs': [{'label': 'display',
          '

In [18]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [19]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng', 'venue.location.city', 'venue.location.formattedAddress']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name       categories        lat       lng  \
0  Hotel Chassieu Best Western plus           Resort  45.737893  4.968213   
1        Intermarché Super et Drive      Supermarket  45.738923  4.958263   
2         ibis Budget Lyon Chassieu            Motel  45.725616  4.968620   
3                         B&B Hotel  Bed & Breakfast  45.724654  4.969357   
4                        Auto Pizza       Food Truck  45.728949  4.952323   

       city                                   formattedAddress  
0  Chassieu         [82 Route De Lyon, 69680 Chassieu, France]  
1  Chassieu         [28 route De Lyon, 69680 Chassieu, France]  
2  Chassieu  [22 Avenue des Frères Montgolfier, 69680 Chass...  
3  Chassieu   [2 rue Augustin Fresnel, 69680 CHASSIEU, France]  
4  Chassieu                                 [Chassieu, France]

In [20]:
def getNearbyVenues(names, latitudes, longitudes, radius=1500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['NOM DE LA COMMUNE', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [21]:
venues = getNearbyVenues(names=df_25min['NOM DE LA COMMUNE'],
                         latitudes=df_25min['latitude'],
                         longitudes=df_25min['longitude']
                                  )
venues.head()

BEYNOST
MIRIBEL
NEYRON
ST MAURICE DE BEYNOST
ST QUENTIN FALLAVIER
VAULX MILIEU
VILLEFONTAINE
CHARVIEU CHAVAGNEUX
PONT DE CHERUY
ANTHON
JANNEYRIAS
VILLETTE D ANTHON
FRONTONAS
SATOLAS ET BONCE
LA VERPILLIERE
GRENAY
HEYRIEUX
DIEMOZ
LYON 03
LYON 06
LYON 07
LYON 08
LYON 09
VILLEURBANNE
VAULX EN VELIN
COLOMBIER SAUGNIEU
RILLIEUX LA PAPE
DECINES CHARPIEU
ST FONS
VENISSIEUX
CAILLOUX SUR FONTAINES
CALUIRE ET CUIRE
PIERRE BENITE
FEYZIN
JONAGE
JONS
MEYZIEU
PUSIGNAN
LA MULATIERE
COMMUNAY
ST SYMPHORIEN D OZON
SEREZIN DU RHONE
SIMANDRES
SOLAIZE
TERNAY
CHARLY
VERNAISON
BRON
IRIGNY
SATHONAY CAMP
SATHONAY VILLAGE
CHASSIEU
ST BONNET DE MURE
ST LAURENT DE MURE
GENAS
MIONS
ST PIERRE DE CHANDIEU
TOUSSIEU
ST PRIEST
CORBAS
CHAPONNAY
MARENNES


NOM DE LA COMMUNE  Neighborhood Latitude  Neighborhood Longitude  \
0           BEYNOST              45.839033                4.997380   
1           BEYNOST              45.839033                4.997380   
2           BEYNOST              45.839033                4.997380   
3           BEYNOST              45.839033                4.997380   
4            NEYRON              45.818419                4.930905   

                         Venue  Venue Latitude  Venue Longitude  \
0         Gare SNCF de Beynost       45.833659         5.006286   
1                            Z       45.840060         5.002060   
2     Entreprise Auclair Herve       45.832186         5.005918   
3  GSF ORION - Plaine De L'ain       45.828931         5.004067   
4      Auberge De Saint Didier       45.820906         4.929995   

     Venue Category  
0     Train Station  
1        Kids Store  
2     Auto Workshop  
3  Business Service  
4        Restaurant

Many cities don't have enough venues to make a proper analysis. 

Then, we will remove cities (or, let's say villages!) which have less than 5 venues (5 excluded)

We will at the end include them again in a cluster => the village cluster!

In [96]:
# As many cities (villages!) don't have a lot of venues, we will drop cities with less than 10 venues

count_venues = venues.groupby('NOM DE LA COMMUNE').count()

# We keep only cities with more than 5 venues (or equal)

at_least_n_venues = count_venues[count_venues['Venue']>4]

# As we kept only cities with more than 5 venues, we can consider these are cities (others are villages)

keep_or_not = []

for i in range(venues['NOM DE LA COMMUNE'].str.split(",").size):
    
    if venues['NOM DE LA COMMUNE'][i] in at_least_n_venues.index:
        keep_or_not.append(True)
    else:
        keep_or_not.append(False)


venues_cities = venues[keep_or_not]

In [97]:
# one hot encoding
onehot = pd.get_dummies(venues_cities[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
onehot['NOM DE LA COMMUNE'] = venues_cities['NOM DE LA COMMUNE'] 

# move neighborhood column to the first column
fixed_columns = [onehot.columns[-1]] + list(onehot.columns[:-1])
onehot = onehot[fixed_columns]

# Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category
grouped = onehot.groupby('NOM DE LA COMMUNE').mean().reset_index()
grouped.head()

NOM DE LA COMMUNE  Airport  Art Gallery  Art Museum  Asian Restaurant  \
0              BRON      0.0          0.0        0.00               0.0   
1  CALUIRE ET CUIRE      0.0          0.0        0.04               0.0   
2          CHASSIEU      0.0          0.0        0.00               0.0   
3            CORBAS      0.2          0.0        0.00               0.0   
4  DECINES CHARPIEU      0.0          0.0        0.00               0.0   

   Auto Garage  Auto Workshop  Automotive Shop  BBQ Joint  Bakery  ...  \
0          0.0          0.000              0.0       0.00     0.0  ...   
1          0.0          0.000              0.0       0.04     0.0  ...   
2          0.0          0.000              0.0       0.00     0.0  ...   
3          0.0          0.000              0.0       0.00     0.0  ...   
4          0.0          0.125              0.0       0.00     0.0  ...   

   Train Station  Tram Station  Video Game Store  Vietnamese Restaurant  \
0            0.0      0.272727               0.0                    0.0   
1            0.0      0.000000               0.0                    0.0   
2            0.0      0.111111               0.0                    0.0   
3            0.0      0.000000               0.0                    0.0   
4            0.0      0.000000               0.0                    0.0   

   Water Park  Wine Bar  Wine Shop  Women's Store  Zoo  Zoo Exhibit  
0    0.090909       0.0        0.0            0.0  0.0          0.0  
1    0.000000       0.0        0.0            0.0  0.0          0.0  
2    0.000000       0.0        0.0            0.0  0.0          0.0  
3    0.000000       0.0        0.0            0.0  0.0          0.0  
4    0.000000       0.0        0.0            0.0  0.0          0.0  

[5 rows x 156 columns]

In [98]:
# We look for the top 5 venues for each cities

num_top_venues = 5

for hood in grouped['NOM DE LA COMMUNE']:
    print("----"+hood+"----")
    temp = grouped[grouped['NOM DE LA COMMUNE'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----BRON----
                  venue  freq
0          Tram Station  0.27
1                 Hotel  0.18
2  Fast Food Restaurant  0.09
3      Department Store  0.09
4             Cafeteria  0.09


----CALUIRE ET CUIRE----
               venue  freq
0              Hotel  0.12
1  French Restaurant  0.08
2        Supermarket  0.08
3       Concert Hall  0.08
4          Multiplex  0.04


----CHASSIEU----
              venue  freq
0  Kebab Restaurant  0.11
1      Tram Station  0.11
2        Restaurant  0.11
3        Food Truck  0.11
4      Optical Shop  0.11


----CORBAS----
               venue  freq
0            Airport   0.2
1        Supermarket   0.2
2  French Restaurant   0.2
3       Optical Shop   0.2
4     Rental Service   0.2


----DECINES CHARPIEU----
                venue  freq
0  Light Rail Station  0.25
1          Restaurant  0.12
2         Supermarket  0.12
3       Auto Workshop  0.12
4    Botanical Garden  0.12


----FEYZIN----
                        venue  freq
0               

In [99]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [100]:
num_top_venues = 5

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['NOM DE LA COMMUNE']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
venues_sorted = pd.DataFrame(columns=columns)
venues_sorted['NOM DE LA COMMUNE'] = grouped['NOM DE LA COMMUNE']

for ind in np.arange(grouped.shape[0]):
    venues_sorted.iloc[ind, 1:] = return_most_common_venues(grouped.iloc[ind, :], num_top_venues)

venues_sorted


NOM DE LA COMMUNE       1st Most Common Venue 2nd Most Common Venue  \
0                    BRON                Tram Station                 Hotel   
1        CALUIRE ET CUIRE                       Hotel     French Restaurant   
2                CHASSIEU                       Motel           Golf Course   
3                  CORBAS                     Airport          Optical Shop   
4        DECINES CHARPIEU          Light Rail Station                 Plaza   
5                  FEYZIN  Construction & Landscaping          Concert Hall   
6               FRONTONAS                Dance Studio           IT Services   
7              JANNEYRIAS            Business Service    Child Care Service   
8            LA MULATIERE                       Hotel     French Restaurant   
9          LA VERPILLIERE                 Supermarket          Home Service   
10                LYON 03           French Restaurant            Restaurant   
11                LYON 06           French Restaurant                 Hotel   
12                LYON 07                       Hotel     French Restaurant   
13                LYON 08                      Museum                 Hotel   
14                LYON 09           French Restaurant                 Hotel   
15                MEYZIEU                 Supermarket     French Restaurant   
16          PIERRE BENITE        Fast Food Restaurant           Supermarket   
17         PONT DE CHERUY               Shopping Mall            Shoe Store   
18               PUSIGNAN  Construction & Landscaping                Bakery   
19       RILLIEUX LA PAPE      Furniture / Home Store        Clothing Store   
20          SATHONAY CAMP                Soccer Field           Gas Station   
21       SEREZIN DU RHONE                       Hotel             Rest Area   
22                SOLAIZE                 Pizza Place             Rest Area   
23      ST BONNET DE MURE      Furniture / Home Store           Supermarket   
24                ST FONS                Tram Station           Supermarket   
25  ST MAURICE DE BEYNOST                 Supermarket           IT Services   
26              ST PRIEST                Tram Station   Indie Movie Theater   
27   ST QUENTIN FALLAVIER                  Restaurant            Toll Plaza   
28   ST SYMPHORIEN D OZON                      Garden                 Plaza   
29                 TERNAY               Auto Workshop   Rental Car Location   
30         VAULX EN VELIN                 Bus Station           Snack Place   
31             VENISSIEUX                Tram Station              Pharmacy   
32          VILLEFONTAINE          Italian Restaurant         Auto Workshop   
33           VILLEURBANNE                 Supermarket                   Bar   

         3rd Most Common Venue    4th Most Common Venue  \
0           Chinese Restaurant              Gas Station   
1                 Concert Hall              Supermarket   
2                       Resort               Restaurant   
3            French Restaurant              Supermarket   
4                   Restaurant            Auto Workshop   
5                  Gas Station                    Hotel   
6                        Hotel          Automotive Shop   
7              Automotive Shop             Home Service   
8               Sandwich Place              Pizza Place   
9         Fast Food Restaurant            Train Station   
10                       Hotel                      Bar   
11                       Plaza                      Pub   
12              Soccer Stadium                      Bar   
13                Tram Station                    Plaza   
14                  Restaurant         Department Store   
15          Light Rail Station               Restaurant   
16         Rental Car Location               Canal Lock   
17                      Market            Women's Store   
18                  Restaurant                  Factory   
19           French Restaurant              Supermarket   
20 

# 5. Clustering cities

In [101]:
grouped_clustering = grouped.drop('NOM DE LA COMMUNE', 1)

In [102]:
# set number of clusters
kclusters = 3

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_

array([0, 1, 2, 2, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 2, 2, 1, 1, 1, 1, 1,
       1, 1, 0, 2, 0, 1, 1, 1, 1, 0, 1, 2])

In [103]:
# add clustering labels
venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

In [104]:
merged = df_25min

# merge to add latitude/longitude for each neighborhood
merged = merged.join(venues_sorted.set_index('NOM DE LA COMMUNE'), on='NOM DE LA COMMUNE')

# We fill a new cluster for cities with less than 5 venues => this cluster is for villages!
values = {'Cluster Labels': kclusters }
merged = merged.fillna(value=values)

merged.head()# check the last columns!

level_0  index CODE INSEE      NOM DE LA COMMUNE  CODE POSTAL  \
18      392    395      01043                BEYNOST         1700   
19      393    396      01249                MIRIBEL         1700   
20      394    397      01275                 NEYRON         1700   
21      395    398      01376  ST MAURICE DE BEYNOST         1700   
28      420  14717      38449   ST QUENTIN FALLAVIER        38070   

   LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept            STATUT  \
18                BEYNOST     65285.0  RHONE-ALPES      AIN    Commune simple   
19                MIRIBEL     65290.0  RHONE-ALPES      AIN  Chef-lieu canton   
20                 NEYRON     65261.0  RHONE-ALPES      AIN    Commune simple   
21  ST MAURICE DE BEYNOST     65280.0  RHONE-ALPES      AIN    Commune simple   
28   ST QUENTIN FALLAVIER     65066.0  RHONE-ALPES    ISERE    Commune simple   

    ...  longitude  Distance from chassieu  Distance chassieu (km)  \
18  ...   4.997380               12.243608                    20.5   
19  ...   4.941067               12.663058                    20.0   
20  ...   4.930905               10.005722                    17.0   
21  ...   4.977262               11.492164                    22.0   
28  ...   5.108568               15.201457                    20.0   

   Time chassieu (min)  Cluster Labels 1st Most Common Venue  \
18                24.5             3.0                   NaN   
19                22.5             3.0                   NaN   
20                18.5             3.0                   NaN   
21                24.5             2.0           Supermarket   
28                18.0             1.0            Restaurant   

    2nd Most Common Venue  3rd Most Common Venue    4th Most Common Venue  \
18                    NaN                    NaN                      NaN   
19                    NaN                    NaN                      NaN   
20                    NaN                    NaN                      NaN   
21            IT Services          Train Station  Health & Beauty Service   
28             Toll Plaza                  Hotel            Auto Workshop   

    5th Most Common Venue  
18                    NaN  
19                    NaN  
20                    NaN  
21            Zoo Exhibit  
28          Train Station  

[5 rows x 35 columns]

In [105]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)+1))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['latitude'], merged['longitude'], merged['NOM DE LA COMMUNE'], merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [106]:
map_clusters = folium.Map(location=coords_chassieu, zoom_start=11)

map_clusters.choropleth(
    geo_data= cities_json,
    data= df_test3,
    columns=['CODE INSEE', 'Time chassieu (min)'],
    key_on='feature.properties.code',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.3,
    legend_name='Travel time from chassieu'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)+1))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['latitude'], merged['longitude'], merged['NOM DE LA COMMUNE'], merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(int(cluster)) , parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)

# display map
map_clusters

# 6. Examine Clusters

### Cluster 1

In [32]:
merged.loc[merged['Cluster Labels'] == 0, merged.columns[[1] + list(range(5, merged.shape[1]))]].head()

index LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept  \
93   28467                ST FONS     65129.0  RHONE-ALPES    RHONE   
94   28468             VENISSIEUX     65133.0  RHONE-ALPES    RHONE   
146  28605                   BRON     65167.0  RHONE-ALPES    RHONE   
176  28702              ST PRIEST     65131.0  RHONE-ALPES    RHONE   

               STATUT  Code Region  Code Commune  Z Moyen Code Dept  ...  \
93   Chef-lieu canton         82.0         199.0    177.0        69  ...   
94   Chef-lieu canton         82.0         259.0    195.0        69  ...   
146  Chef-lieu canton         82.0          29.0    198.0        69  ...   
176  Chef-lieu canton         82.0         290.0    215.0        69  ...   

     longitude Distance from chassieu  Distance chassieu (km)  \
93    4.850464               9.449270                    14.0   
94    4.881377               7.118356                    10.5   
146   4.911682               4.075860                     5.0   
176   4.948821               3.527144                     3.0   

     Time chassieu (min)  Cluster Labels  1st Most Common Venue  \
93                  16.5             0.0           Tram Station   
94                  17.0             0.0           Tram Station   
146                 10.5             0.0           Tram Station   
176                  5.5             0.0           Tram Station   

     2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
93             Supermarket                 Hotel    Rental Car Location   
94                Pharmacy           Flea Market   Fast Food Restaurant   
146                  Hotel    Chinese Restaurant            Gas Station   
176    Indie Movie Theater          Home Service         Massage Studio   

     5th Most Common Venue  
93             Auto Garage  
94            Concert Hall  
146             Water Park  
176            Pizza Place  

[4 rows x 31 columns]

This cluster is composed of Tram station, fast food and supermarket / shop

It's a suburb cluster with public transport as Tram.

It would be nice to live. And it is also very close from Chassieu.

### Cluster 2

In [33]:
merged.loc[merged['Cluster Labels'] == 1, merged.columns[[1] + list(range(5, merged.shape[1]))]].head()

index LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept  \
28  14717   ST QUENTIN FALLAVIER     65066.0  RHONE-ALPES    ISERE   
35  14725          VILLEFONTAINE     65038.0  RHONE-ALPES    ISERE   
44  14847         PONT DE CHERUY     65192.0  RHONE-ALPES    ISERE   
47  14887             JANNEYRIAS     65190.0  RHONE-ALPES    ISERE   
49  14889              FRONTONAS     65080.0  RHONE-ALPES    ISERE   

              STATUT  Code Region  Code Commune  Z Moyen Code Dept  ...  \
28    Commune simple         82.0         449.0    262.0        38  ...   
35  Chef-lieu canton         82.0         553.0    280.0        38  ...   
44  Chef-lieu canton         82.0         316.0    207.0        38  ...   
47    Commune simple         82.0         197.0    240.0        38  ...   
49    Commune simple         82.0         176.0    239.0        38  ...   

    longitude Distance from chassieu  Distance chassieu (km)  \
28   5.108568              15.201457                    20.0   
35   5.155477              19.855999                    26.0   
44   5.173142              16.442126                    20.5   
47   5.114483              11.926786                    17.0   
49   5.185821              19.453692                    28.5   

    Time chassieu (min)  Cluster Labels  1st Most Common Venue  \
28                 18.0             1.0             Restaurant   
35                 21.5             1.0     Italian Restaurant   
44                 23.5             1.0          Shopping Mall   
47                 20.0             1.0       Business Service   
49                 24.0             1.0           Dance Studio   

    2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
28             Toll Plaza                 Hotel          Auto Workshop   
35          Auto Workshop       Automotive Shop            Supermarket   
44             Shoe Store                Market          Women's Store   
47     Child Care Service       Automotive Shop           Home Service   
49            IT Services                 Hotel        Automotive Shop   

    5th Most Common Venue  
28          Train Station  
35          Shopping Mall  
44      Mobile Phone Shop  
47            Zoo Exhibit  
49           Home Service  

[5 rows x 31 columns]

It's almost the same cluster than cluster 1 but there is less public transport.

It is then a suburb cluster with less public transport. That would also be cool to live there. It's quite close to Chassieu.

### Cluster 3

In [34]:
merged.loc[merged['Cluster Labels'] == 2, merged.columns[[1] + list(range(5, merged.shape[1]))]].head()

index LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept  \
21     398  ST MAURICE DE BEYNOST     65280.0  RHONE-ALPES      AIN   
51   14891         LA VERPILLIERE     65065.0  RHONE-ALPES    ISERE   
84   28448           VILLEURBANNE     65207.0  RHONE-ALPES    RHONE   
91   28456       DECINES CHARPIEU     65210.0  RHONE-ALPES    RHONE   
117  28513          PIERRE BENITE     65130.0  RHONE-ALPES    RHONE   

               STATUT  Code Region  Code Commune  Z Moyen Code Dept  ...  \
21     Commune simple         82.0         376.0    230.0         1  ...   
51   Chef-lieu canton         82.0         537.0    220.0        38  ...   
84   Chef-lieu canton         82.0         266.0    175.0        69  ...   
91   Chef-lieu canton         82.0         275.0    189.0        69  ...   
117    Commune simple         82.0         152.0    173.0        69  ...   

     longitude Distance from chassieu  Distance chassieu (km)  \
21    4.977262              11.492164                    22.0   
51    5.149155              17.796280                    24.5   
84    4.888458               7.319184                    13.5   
91    4.961427               4.486186                     7.5   
117   4.827050              11.135161                    20.0   

     Time chassieu (min)  Cluster Labels  1st Most Common Venue  \
21                  24.5             2.0            Supermarket   
51                  22.5             2.0            Supermarket   
84                  19.0             2.0            Supermarket   
91                  11.5             2.0     Light Rail Station   
117                 21.5             2.0   Fast Food Restaurant   

     2nd Most Common Venue 3rd Most Common Venue    4th Most Common Venue  \
21             IT Services         Train Station  Health & Beauty Service   
51            Home Service  Fast Food Restaurant            Train Station   
84                     Bar              Bus Stop     Fast Food Restaurant   
91                   Plaza            Restaurant            Auto Workshop   
117            Supermarket   Rental Car Location               Canal Lock   

     5th Most Common Venue  
21             Zoo Exhibit  
51       Electronics Store  
84                  Bakery  
91        Botanical Garden  
117                  Hotel  

[5 rows x 31 columns]

This cluster is principally composed of Bar, Hotel, Business, Shop.$

It's clearly a cluster of a city center, in this case, lyon's center. 

There are some cities of this cluster in noise in the country side (because small villages can have a bar and some shops).

### Cluster 4

In [35]:
merged.loc[merged['Cluster Labels'] == 3, merged.columns[[1] + list(range(5, merged.shape[1]))]].head()

index LIBELLE D'ACHEMINEMENT  Y Centroid   Nom Region Nom Dept  \
18    395                BEYNOST     65285.0  RHONE-ALPES      AIN   
19    396                MIRIBEL     65290.0  RHONE-ALPES      AIN   
20    397                 NEYRON     65261.0  RHONE-ALPES      AIN   
34  14724           VAULX MILIEU     65041.0  RHONE-ALPES    ISERE   
42  14845    CHARVIEU CHAVAGNEUX     65178.0  RHONE-ALPES    ISERE   

              STATUT  Code Region  Code Commune  Z Moyen Code Dept  ...  \
18    Commune simple         82.0          43.0    237.0         1  ...   
19  Chef-lieu canton         82.0         249.0    260.0         1  ...   
20    Commune simple         82.0         275.0    241.0         1  ...   
34    Commune simple         82.0         530.0    241.0        38  ...   
42    Commune simple         82.0          85.0    217.0        38  ...   

    longitude Distance from chassieu  Distance chassieu (km)  \
18   4.997380              12.243608                    20.5   
19   4.941067              12.663058                    20.0   
20   4.930905              10.005722                    17.0   
34   5.185985              21.571059                    26.0   
42   5.151117              14.604596                    20.5   

    Time chassieu (min)  Cluster Labels  1st Most Common Venue  \
18                 24.5             3.0                    NaN   
19                 22.5             3.0                    NaN   
20                 18.5             3.0                    NaN   
34                 20.5             3.0                    NaN   
42                 23.5             3.0                    NaN   

    2nd Most Common Venue 3rd Most Common Venue  4th Most Common Venue  \
18                    NaN                   NaN                    NaN   
19                    NaN                   NaN                    NaN   
20                    NaN                   NaN                    NaN   
34                    NaN                   NaN                    NaN   
42                    NaN                   NaN                    NaN   

    5th Most Common Venue  
18                    NaN  
19                    NaN  
20                    NaN  
34                    NaN  
42                    NaN  

[5 rows x 31 columns]

It's the cluster where there are less than 5 venues.

This cluster is representing small villages. It could be cool to live there in order to have our own house with a lower price.

But this is also further to our work and we won't have close activities and close shops.

# 7. Final Map

In this section, we will provide a map with a full range of details in order to facilitate the choice of the customers.

In [43]:
# Let's give a name to clusters

Clusters_name = ["Suburb with public transports", "City center", "Suburb", "Villages"]

In [113]:
map_clusters = folium.Map(location=coords_chassieu, zoom_start=11)

map_clusters.choropleth(
    geo_data= cities_json,
    data= df_test3,
    columns=['CODE INSEE', 'Time chassieu (min)'],
    key_on='feature.properties.code',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.3,
    legend_name='Travel time from chassieu'
)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)+1))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(merged['latitude'], merged['longitude'], merged['NOM DE LA COMMUNE'], merged['Cluster Labels']):
    label = folium.Popup( str(poi) + ' Cluster ' + Clusters_name[(int(cluster))] , parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster)-1],
        fill=True,
        fill_color=rainbow[int(cluster)-1],
        fill_opacity=0.7).add_to(map_clusters)

# display map
map_clusters

# Conclusion

In conclusion, this analysis is giving us the possibilies of location to explore.

We are not really sure of which cluster we will choose.

On the first hand, countryside has big avantages, like having a house, for a lower price. But also a long travel to work...

On the other, commodities from the 2 suburb clusters are really appreciable. But it will be more expensive!

What is sure is that we will look at the choropleth map of travel time closely because we want to minimize travel time to work.

The next step of this analysis is exporting average price of flat/appartment for each cities in order to facilitate the choice. I tried to to it but this information is protected on many websites.

Also, Foursquare is not very popular in France, so results are not very accurate and meaningfull. This analysis would have be better in US for example.

##### I hope you enjoyed my analysis! :)